In [5]:
from transformers import Wav2Vec2FeatureExtractor, WavLMForXVector
import torch
import subprocess
import librosa
import os
import soundfile as sf  
from tqdm import tqdm
from itertools import combinations
import pandas as pd
import numpy as np
import random
import matplotlib.pyplot as plt
from sklearn.metrics import homogeneity_score, completeness_score, v_measure_score
from sklearn.cluster import KMeans

/home/andrea-gariboldi/anaconda3/envs/speech_env/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


### Delete the unecessary files for the project

In [2]:
# Clear dataset. Delete all files not needed for the assignment. Just keep the ones with shortpassage in the filename (Run once - set flag)
flag = False

if flag:
    directory = "data/ABI-3_Corpus"  
    subprocess.run(f"find {directory} -type f ! -name '*shortpassage*.wav' -delete", shell=True)

### Resampling (from 22050Hz to 16000Hz)
This phase is necessary as the WavLm model expects the data to be sampled at 16000Hz. Using librosa.resample for resampling.

In [ ]:
def resample_dataset(root_dir, target_sr=16000):
    """
    Resample all WAV files in a directory tree to the target sample rate.
    
    Args:
        root_dir (str): Root directory containing WAV files
        target_sr (int): Target sample rate in Hz
    """
    total_files = 0
    resampled_files = 0
    
    for dirpath, _, filenames in os.walk(root_dir):
        wav_files = [f for f in filenames if f.lower().endswith('.wav')]
        
        for filename in wav_files:
            total_files += 1
            full_path = os.path.join(dirpath, filename)
            
            try:
                sr = librosa.get_samplerate(full_path) #check sample rate
                
                if sr != target_sr:
                    y, _ = librosa.load(full_path, sr=sr)
                    
                    # Resample
                    y_resampled = librosa.resample(y, orig_sr=sr, target_sr=target_sr)
                    
                    sf.write(full_path, y_resampled, target_sr)
                    
                    resampled_files += 1
                    if resampled_files % 100 == 0:  # Progress update
                        print(f"Resampled {resampled_files} files...")
                        
            except Exception as e:
                print(f"Error processing {full_path}: {str(e)}")
    
    print(f"\nResampling complete. Processed {total_files} files, resampled {resampled_files} files.")
resample_dataset("data/ABI-3_Corpus")

Resampled 100 files...
Resampled 200 files...
Resampled 300 files...
Resampled 400 files...
Resampled 500 files...
Resampled 600 files...
Resampled 700 files...
Resampled 800 files...

Resampling complete. Processed 855 files, resampled 854 files.


### First approach for data augmentation
Split each wav files into three separate files.

In [ ]:
#TESTING. DO not put in production. For each wav file in the dataset, create three separate files (each one has 1/3 of the length of the original file). This is done recursively

flag = False
if flag:
    def split_wav(input_file, num_parts=3, delete_original=True):
        y, sr = librosa.load(input_file, sr=16000)
        
        directory = os.path.dirname(input_file)
        base_filename = os.path.splitext(os.path.basename(input_file))[0]
        
        # Calculate part length
        part_length = len(y) // num_parts
        
        # Split and save parts
        for i in range(num_parts):
            output_filename = os.path.join(directory, f"{base_filename}{i+1}.wav")
            
            start_idx = i * part_length
            end_idx = len(y) if i == num_parts - 1 else (i + 1) * part_length
            
            # Extract and save chunk
            sf.write(output_filename, y[start_idx:end_idx], sr)
            print(f"Created {output_filename}")
        if delete_original:
                os.remove(input_file)
                print(f"Deleted original file: {input_file}")

    def process_directory(root_dir, num_parts=3):
        """
        Recursively process all WAV files in a directory and its subdirectories.
        
        Args:
            root_dir (str): Root directory to start searching from
            num_parts (int): Number of parts to split each WAV file into
        """
        processed_count = 0
        
        # Walk through directory tree
        for dirpath, dirnames, filenames in os.walk(root_dir):
            for filename in filenames:
                if filename.lower().endswith('.wav'):
                    # Skip files that might already be split (ending with a digit)
                    if not (filename[-5].isdigit() and filename[-6:-4] == '.wav'):
                        full_path = os.path.join(dirpath, filename)
                        try:
                            split_wav(full_path, num_parts)
                            processed_count += 1
                        except Exception as e:
                            print(f"Error processing {full_path}: {e}")
        
        print(f"Total WAV files processed: {processed_count}")

    root_directory = "data/ABI-1 Corpus/accents"
    process_directory(root_directory, 3)

### Second approach for data augmemtation
Use a sliding window approach, split each .wav file into files of 10 seconds duration, with 5 seconds overlap

In [ ]:
#Sliding window

flag = False
if flag:
    def split_wav_sliding_window(input_file, window_duration=10, overlap_duration=5, delete_original=True):
        """
        Split a WAV file using a sliding window approach with overlap.
        
        Args:
            input_file (str): Path to the input WAV file
            window_duration (float): Duration of each window in seconds
            overlap_duration (float): Duration of overlap between windows in seconds
            delete_original (bool): Whether to delete the original file after processing
        """
        y, sr = librosa.load(input_file, sr=16000)
        
        directory = os.path.dirname(input_file)
        base_filename = os.path.splitext(os.path.basename(input_file))[0]
        
        # Calculate window and hop size in samples
        window_size = int(window_duration * sr)
        hop_size = int((window_duration - overlap_duration) * sr)
        
        # Calculate number of windows
        total_duration = len(y) / sr
        num_windows = max(1, int((total_duration - overlap_duration) / (window_duration - overlap_duration)))
        
        for i in range(num_windows):
            start_idx = i * hop_size
            end_idx = min(start_idx + window_size, len(y))
            
            # Skip if window is too small (might happen for the last window)
            if end_idx - start_idx < 0.5 * window_size:
                continue
            
            output_filename = os.path.join(directory, f"{base_filename}_win{i+1}.wav")
    
            sf.write(output_filename, y[start_idx:end_idx], sr)
            print(f"Created {output_filename}")
        
        if delete_original:
            os.remove(input_file)
            print(f"Deleted original file: {input_file}")

    def process_directory(root_dir):
        """
        Recursively process all WAV files in a directory and its subdirectories.
        Args:
            root_dir (str): Root directory to start searching from
        """
        processed_count = 0
        for dirpath, _, filenames in os.walk(root_dir):
            for filename in filenames:
                if filename.lower().endswith('.wav'):
                    # Skip files that might already be split (containing "_win" in their name)
                    if "_win" not in filename:
                        full_path = os.path.join(dirpath, filename)
                        try:
                            split_wav_sliding_window(full_path)
                            processed_count += 1
                        except Exception as e:
                            print(f"Error processing {full_path}: {e}")
        
        print(f"Total WAV files processed: {processed_count}")

    # Usage example
    root_directory = "data/ABI-3_Corpus/accents"
    process_directory(root_directory)

Created data/ABI-3_Corpus/accents/brm_001/male/ars001/shortpassagea_CT_win1.wav
Created data/ABI-3_Corpus/accents/brm_001/male/ars001/shortpassagea_CT_win2.wav
Created data/ABI-3_Corpus/accents/brm_001/male/ars001/shortpassagea_CT_win3.wav
Created data/ABI-3_Corpus/accents/brm_001/male/ars001/shortpassagea_CT_win4.wav
Created data/ABI-3_Corpus/accents/brm_001/male/ars001/shortpassagea_CT_win5.wav
Created data/ABI-3_Corpus/accents/brm_001/male/ars001/shortpassagea_CT_win6.wav
Deleted original file: data/ABI-3_Corpus/accents/brm_001/male/ars001/shortpassagea_CT.wav
Created data/ABI-3_Corpus/accents/brm_001/male/ars001/shortpassagec_CT_win1.wav
Created data/ABI-3_Corpus/accents/brm_001/male/ars001/shortpassagec_CT_win2.wav
Created data/ABI-3_Corpus/accents/brm_001/male/ars001/shortpassagec_CT_win3.wav
Created data/ABI-3_Corpus/accents/brm_001/male/ars001/shortpassagec_CT_win4.wav
Created data/ABI-3_Corpus/accents/brm_001/male/ars001/shortpassagec_CT_win5.wav
Created data/ABI-3_Corpus/acce

### Load the model weights from HuggingFace

In [3]:
feature_extractor = Wav2Vec2FeatureExtractor.from_pretrained('microsoft/wavlm-base-plus-sv')
model = WavLMForXVector.from_pretrained('microsoft/wavlm-base-plus-sv')

### Extract the embeddings for every file

In [ ]:
flag = False
if flag:
    def process_file_embedding(file_path, model, feature_extractor):
        """Generate and save embedding for a single file"""
        try:
            output_path = os.path.splitext(file_path)[0] + '.pt'
            
            if os.path.exists(output_path):
                print(f"Embedding already exists: {output_path}")
                return True
                
            audio, _ = librosa.load(file_path, sr=16000)
            
            # Generate embedding
            inputs = feature_extractor(audio, padding=True, return_tensors="pt")
            embeddings = model(**inputs).embeddings
            embeddings = torch.nn.functional.normalize(embeddings, dim=-1).cpu()
            
            torch.save(embeddings, output_path)
            print(f"Saved embedding: {output_path}")
            return True
            
        except Exception as e:
            print(f"Error processing {file_path}: {e}")
            return False

    def process_directory_embeddings(root_dir, model, feature_extractor):
        """
        Recursively process all WAV files in a directory and its subdirectories,
        generating and saving embeddings.
        """
        processed_count = 0
        error_count = 0
        
        all_wav_files = []
        for dirpath, _, filenames in os.walk(root_dir):
            for filename in filenames:
                if filename.lower().endswith('.wav'):
                    full_path = os.path.join(dirpath, filename)
                    all_wav_files.append(full_path)
        
        for file_path in tqdm(all_wav_files, desc="Processing files"):
            success = process_file_embedding(file_path, model, feature_extractor)
            if success:
                processed_count += 1
            else:
                error_count += 1
        
        print(f"Processing complete!")
        print(f"Total WAV files processed: {processed_count}")
        print(f"Files with errors: {error_count}")

    root_directory = "data/ABI-3_Corpus/accents"
    process_directory_embeddings(root_directory, model, feature_extractor)

Processing files:   0%|          | 0/6948 [00:00<?, ?it/s]It is strongly recommended to pass the ``sampling_rate`` argument to this function. Failing to do so can result in silent errors that might be hard to debug.
/home/andrea-gariboldi/anaconda3/envs/speech_env/lib/python3.10/site-packages/torch/nn/functional.py:5962: UserWarning: Support for mismatched key_padding_mask and attn_mask is deprecated. Use same type for both instead.
  warnings.warn(
Processing files:   0%|          | 1/6948 [00:01<2:40:47,  1.39s/it]It is strongly recommended to pass the ``sampling_rate`` argument to this function. Failing to do so can result in silent errors that might be hard to debug.


Saved embedding: data/ABI-3_Corpus/accents/brm_001/male/ars001/shortpassagec_CT_win4.pt


Processing files:   0%|          | 2/6948 [00:02<2:00:29,  1.04s/it]It is strongly recommended to pass the ``sampling_rate`` argument to this function. Failing to do so can result in silent errors that might be hard to debug.


Saved embedding: data/ABI-3_Corpus/accents/brm_001/male/ars001/shortpassageb_CT_win2.pt


Processing files:   0%|          | 3/6948 [00:02<1:47:56,  1.07it/s]It is strongly recommended to pass the ``sampling_rate`` argument to this function. Failing to do so can result in silent errors that might be hard to debug.


...

Saved embedding: data/ABI-3_Corpus/accents/ilo_001/female/seg001/shortpassagec_CT_win7.pt


Processing files: 100%|█████████▉| 6947/6948 [2:09:35<00:01,  1.33s/it]It is strongly recommended to pass the ``sampling_rate`` argument to this function. Failing to do so can result in silent errors that might be hard to debug.


Saved embedding: data/ABI-3_Corpus/accents/ilo_001/female/seg001/shortpassageb_CT_win1.pt


Processing files: 100%|██████████| 6948/6948 [2:09:36<00:00,  1.12s/it]

Saved embedding: data/ABI-3_Corpus/accents/ilo_001/female/seg001/shortpassagea_CT_win3.pt
Processing complete!
Total WAV files processed: 6948
Files with errors: 0


#### Calculate similarities for each speaker (against itself)
Recursively go through the speakers folders, and compute the Cosine similarity between all the audio file combinations (for the same speaker). Save the results in two csv files:
- all_similarities.csv: for every comparison a row measuring the Cosine similarity between the two files.
- speaker_similarity_summaries.csv: for every speaker, save the number of comparisons, the mean similarity, the median similarity, the minimum similarity, the maximum similarity and the standard deviation

In [ ]:
def process_speakers_recursively(root_dir, output_dir):
    os.makedirs(output_dir, exist_ok=True)
    
    all_summaries = []
    
    all_similarities_file = os.path.join(output_dir, "all_similarities.csv")
    
    with open(all_similarities_file, 'w') as f:
        f.write("accent,gender,speaker,file1,file2,similarity\n")
    
    for accent_dir in tqdm(sorted(os.listdir(root_dir)), desc="Processing accents"):
        accent_path = os.path.join(root_dir, accent_dir)
        
        if not os.path.isdir(accent_path):
            continue
            
        # Process gender directories
        for gender_dir in sorted(os.listdir(accent_path)):
            gender_path = os.path.join(accent_path, gender_dir)
            
            if not os.path.isdir(gender_path):
                continue
                
            for speaker_dir in tqdm(sorted(os.listdir(gender_path)), 
                                   desc=f"Processing {accent_dir}/{gender_dir} speakers",
                                   leave=False):
                speaker_path = os.path.join(gender_path, speaker_dir)
                
                if not os.path.isdir(speaker_path):
                    continue
                    
                # Get all embedding files for current speaker
                embedding_files = [f for f in os.listdir(speaker_path) if f.endswith('.pt')]
                
                if len(embedding_files) < 2:
                    print(f"Warning: Speaker {speaker_path} has fewer than 2 embeddings. Skipping.")
                    continue
                
                process_speaker(
                    speaker_path=speaker_path,
                    embedding_files=embedding_files,
                    accent=accent_dir,
                    gender=gender_dir,
                    speaker=speaker_dir,
                    all_similarities_file=all_similarities_file,
                    all_summaries=all_summaries
                )
    
    pd.DataFrame(all_summaries).to_csv(
        os.path.join(output_dir, "speaker_similarity_summaries.csv"), 
        index=False
    )
    
    print(f"Processing complete. Results saved to {output_dir}")

def process_speaker(speaker_path, embedding_files, accent, gender, speaker, 
                   all_similarities_file, all_summaries):
    """
    Process a single speaker, calculating all pairwise similarities.
    
    Args:
        speaker_path: Path to speaker's directory
        embedding_files: List of embedding filenames
        accent, gender, speaker: Metadata
        all_similarities_file: File to append individual similarities
        all_summaries: List to append summary statistics
    """
    cosine_sim = torch.nn.CosineSimilarity(dim=-1)
    
    combos = list(combinations(embedding_files, 2))
    similarities = []
    
    for file1, file2 in combos:
        path1 = os.path.join(speaker_path, file1)
        path2 = os.path.join(speaker_path, file2)
        
        try:
            embedding1 = torch.load(path1)
            embedding2 = torch.load(path2)
            
            similarity = cosine_sim(embedding1, embedding2).item()
            similarities.append(similarity)
            
            with open(all_similarities_file, 'a') as f:
                f.write(f"{accent},{gender},{speaker},{file1},{file2},{similarity}\n")
                
        except Exception as e:
            print(f"Error processing {path1} and {path2}: {e}")
    
    if similarities:
        summary = {
            'accent': accent,
            'gender': gender,
            'speaker': speaker,
            'num_comparisons': len(similarities),
            'mean_similarity': np.mean(similarities),
            'median_similarity': np.median(similarities),
            'min_similarity': np.min(similarities),
            'max_similarity': np.max(similarities),
            'std_similarity': np.std(similarities)
        }
        all_summaries.append(summary)


root_directory = "data/ABI-3_Corpus/accents"
output_directory = "results/3/same_speaker_similarities"

process_speakers_recursively(root_directory, output_directory)

Processing accents: 100%|██████████| 14/14 [00:35<00:00,  2.50s/it]

Processing complete. Results saved to results/3/same_speaker_similarities


#### Compare similarity between different speakers

In [ ]:
def calculate_cross_speaker_similarities(root_dir, output_dir, samples_per_speaker=5):
    os.makedirs(output_dir, exist_ok=True)
    
    cross_similarities_file = os.path.join(output_dir, "cross_speaker_similarities.csv")
    
    with open(cross_similarities_file, 'w') as f:
        f.write("accent1,gender1,speaker1,accent2,gender2,speaker2,files1,files2,mean_similarity,similarities\n")
    
    all_speakers = []
    
    for accent_dir in tqdm(sorted(os.listdir(root_dir)), desc="Collecting speakers"):
        accent_path = os.path.join(root_dir, accent_dir)
        
        if not os.path.isdir(accent_path):
            continue
            
        for gender_dir in sorted(os.listdir(accent_path)):
            gender_path = os.path.join(accent_path, gender_dir)
            
            if not os.path.isdir(gender_path):
                continue
                
            for speaker_dir in sorted(os.listdir(gender_path)):
                speaker_path = os.path.join(gender_path, speaker_dir)
                
                if not os.path.isdir(speaker_path):
                    continue
                    
                # Only get filenames of embeddings, don't load them
                embedding_files = [f for f in os.listdir(speaker_path) if f.endswith('.pt')]
                
                if len(embedding_files) >= samples_per_speaker:
                    all_speakers.append({
                        'path': speaker_path,
                        'accent': accent_dir,
                        'gender': gender_dir,
                        'speaker': speaker_dir,
                        'embedding_files': embedding_files
                    })
    
    random.seed(42)
    
    cosine_sim = torch.nn.CosineSimilarity(dim=-1)
    
    total_comparisons = 0
    for i, speaker1 in enumerate(tqdm(all_speakers, desc="Comparing different speakers")):
        # For each speaker, compare with subsequent speakers (to avoid duplicates)
        for j, speaker2 in enumerate(all_speakers[i+1:], i+1):
            
            try:
                # Randomly select multiple embedding files from each speaker
                # Use random.sample to get unique files without replacement
                files1 = random.sample(speaker1['embedding_files'], samples_per_speaker)
                files2 = random.sample(speaker2['embedding_files'], samples_per_speaker)
                
                pair_similarities = []
                
                # Compare corresponding samples (1st with 1st, 2nd with 2nd, etc.)
                for idx in range(samples_per_speaker):
                    file1 = files1[idx]
                    file2 = files2[idx]
                    
                    path1 = os.path.join(speaker1['path'], file1)
                    path2 = os.path.join(speaker2['path'], file2)
                    
                    embedding1 = torch.load(path1)
                    embedding2 = torch.load(path2)
                    
                    similarity = cosine_sim(embedding1, embedding2).item()
                    pair_similarities.append(similarity)
                
                mean_similarity = sum(pair_similarities) / len(pair_similarities)
                total_comparisons += 1
                
                with open(cross_similarities_file, 'a') as f:
                    f.write(f"{speaker1['accent']},{speaker1['gender']},{speaker1['speaker']},"
                           f"{speaker2['accent']},{speaker2['gender']},{speaker2['speaker']},"
                           f"{';'.join(files1)},{';'.join(files2)},"
                           f"{mean_similarity},{';'.join(map(str, pair_similarities))}\n")
                
            except Exception as e:
                print(f"Error processing comparison between {speaker1['speaker']} and {speaker2['speaker']}: {e}")
    
    print(f"Processing complete. {total_comparisons} cross-speaker comparisons saved to {cross_similarities_file}")
    return cross_similarities_file

calculate_cross_speaker_similarities("data/ABI-3_Corpus/accents", "results/3/different_speaker_similarities")

Comparing different speakers: 100%|██████████| 285/285 [00:55<00:00,  5.15it/s]

Processing complete. 40470 cross-speaker comparisons saved to results/3/same_speaker_similarities/cross_speaker_similarities.csv


'results/3/same_speaker_similarities/cross_speaker_similarities.csv'

### Find optimal threshold
Try from 0 to 1 (0.1 step) to find the optimal threshold. The optimal threshold is measured based on different metrics (accuracy, precision, recall, f1 score, far and frr).
Plot the distributions for same and different speakers similarity, and the plot the metrics of the system at different threshold values.

In [ ]:
def find_optimal_threshold(same_speaker_file, cross_speaker_file, output_dir):
    os.makedirs(output_dir, exist_ok=True)
    
    same_df = pd.read_csv(same_speaker_file)
    cross_df = pd.read_csv(cross_speaker_file)
    
    same_similarities = same_df['similarity'].values    
    cross_similarities = cross_df['mean_similarity'].values
    
    thresholds = np.linspace(0, 1, 101)  # 0 to 1 in steps of 0.01
    
    results = []
    
    for threshold in thresholds:
        true_positives = np.sum(same_similarities >= threshold)
        false_negatives = np.sum(same_similarities < threshold)
        
        true_negatives = np.sum(cross_similarities < threshold)
        false_positives = np.sum(cross_similarities >= threshold)
        
        accuracy = (true_positives + true_negatives) / (true_positives + true_negatives + false_positives + false_negatives)
        
        precision = true_positives / (true_positives + false_positives) if (true_positives + false_positives) > 0 else 0
        recall = true_positives / (true_positives + false_negatives) if (true_positives + false_negatives) > 0 else 0
        
        f1_score = 2 * (precision * recall) / (precision + recall) if (precision + recall) > 0 else 0
        
        far = false_positives / (false_positives + true_negatives) if (false_positives + true_negatives) > 0 else 0
        frr = false_negatives / (false_negatives + true_positives) if (false_negatives + true_positives) > 0 else 0
        
        results.append({
            'threshold': threshold,
            'accuracy': accuracy,
            'precision': precision,
            'recall': recall,
            'f1_score': f1_score,
            'far': far,
            'frr': frr,
            'true_positives': true_positives,
            'true_negatives': true_negatives,
            'false_positives': false_positives,
            'false_negatives': false_negatives
        })
    
    results_df = pd.DataFrame(results)
    
    optimal = {
        'max_accuracy': {
            'threshold': results_df.loc[results_df['accuracy'].idxmax()]['threshold'],
            'value': results_df['accuracy'].max()
        },
        'max_f1': {
            'threshold': results_df.loc[results_df['f1_score'].idxmax()]['threshold'],
            'value': results_df['f1_score'].max()
        }
    }
    
    # Find Equal Error Rate (EER)
    # EER is the point where FAR = FRR
    eer_idx = np.argmin(np.abs(results_df['far'] - results_df['frr']))
    optimal['eer'] = {
        'threshold': results_df.iloc[eer_idx]['threshold'],
        'value': (results_df.iloc[eer_idx]['far'] + results_df.iloc[eer_idx]['frr']) / 2
    }
    
    results_df.to_csv(os.path.join(output_dir, 'threshold_analysis.csv'), index=False)
    
    plot_threshold_analysis(results_df, optimal, output_dir)
    plot_similarity_distributions(same_similarities, cross_similarities, optimal, output_dir)
    
    return optimal

def plot_threshold_analysis(results_df, optimal, output_dir):
    plt.figure(figsize=(12, 8))
    
    # Plot accuracy, precision, recall, F1
    plt.plot(results_df['threshold'], results_df['accuracy'], label='Accuracy')
    plt.plot(results_df['threshold'], results_df['precision'], label='Precision')
    plt.plot(results_df['threshold'], results_df['recall'], label='Recall')
    plt.plot(results_df['threshold'], results_df['f1_score'], label='F1 Score')
    
    # Plot FAR and FRR
    plt.plot(results_df['threshold'], results_df['far'], label='False Acceptance Rate (FAR)')
    plt.plot(results_df['threshold'], results_df['frr'], label='False Rejection Rate (FRR)')
    
    # Mark optimal points
    plt.axvline(x=optimal['max_accuracy']['threshold'], color='green', linestyle='--', 
                linewidth=2.5, label=f"Max Accuracy: {optimal['max_accuracy']['threshold']:.2f}")
    plt.axvline(x=optimal['max_f1']['threshold'], color='blue', linestyle=':', 
                linewidth=3.5, label=f"Max F1: {optimal['max_f1']['threshold']:.2f}")
    plt.axvline(x=optimal['eer']['threshold'], color='red', linestyle='-', 
                linewidth=1.5, label=f"EER: {optimal['eer']['threshold']:.2f}")
    
    plt.xlabel('Threshold')
    plt.ylabel('Value')
    plt.title('Evaluation Metrics vs Threshold')
    plt.legend()
    plt.grid(True)
    plt.savefig(os.path.join(output_dir, 'threshold_metrics.png'))
    plt.close()

def plot_similarity_distributions(same_similarities, cross_similarities, optimal, output_dir):
    plt.figure(figsize=(12, 8))
    
    plt.rcParams.update({
        'font.size': 14,
        'axes.labelsize': 16,
        'axes.titlesize': 18,
        'xtick.labelsize': 14,
        'ytick.labelsize': 14,
        'legend.fontsize': 14
    })
    
    # Plot histograms
    plt.hist(same_similarities, bins=50, alpha=0.5, label='Same Speaker')
    plt.hist(cross_similarities, bins=50, alpha=0.5, label='Different Speakers')
    
    plt.xlabel('Cosine Similarity', fontsize=16)
    plt.ylabel('Frequency', fontsize=16)
    plt.title('Distribution of Similarities', fontsize=18, pad=20)
    plt.legend(prop={'size': 14})
    plt.grid(True)
    plt.tight_layout()
    plt.savefig(os.path.join(output_dir, 'similarity_distributions2.png'), dpi=300, bbox_inches='tight')
    plt.close()

find_optimal_threshold(
    "results/3/same_speaker_similarities/all_similarities.csv", 
    "results/3/different_speaker_similarities/cross_speaker_similarities.csv", 
    "results/3/threshold_analysis"
)

{'max_accuracy': {'threshold': np.float64(0.93),
  'value': np.float64(0.9808935497773309)},
 'max_f1': {'threshold': np.float64(0.93),
  'value': np.float64(0.9862080633981543)},
 'eer': {'threshold': np.float64(0.93),
  'value': np.float64(0.021266870635178445)}}

### Clustering
Using k-means with k as the number of speakers

In [ ]:
def collect_embeddings_for_clustering(root_dir):
    all_embeddings = []
    speaker_labels = []
    accent_labels = [] # later for visualization
    
    random.seed(42)
    
    for accent_dir in tqdm(sorted(os.listdir(root_dir)), desc="Collecting embeddings"):
        accent_path = os.path.join(root_dir, accent_dir)
        
        if not os.path.isdir(accent_path):
            continue
            
        # Process gender directories
        for gender_dir in sorted(os.listdir(accent_path)):
            gender_path = os.path.join(accent_path, gender_dir)
            
            if not os.path.isdir(gender_path):
                continue
                
            # Process speaker directories
            for speaker_dir in tqdm(sorted(os.listdir(gender_path)), 
                                   desc=f"Processing {accent_dir}/{gender_dir} speakers",
                                   leave=False):
                speaker_path = os.path.join(gender_path, speaker_dir)
                
                if not os.path.isdir(speaker_path):
                    continue
                    
                embedding_files = [f for f in os.listdir(speaker_path) if f.endswith('.pt')]
                
                if len(embedding_files) == 0:
                    continue
                
                for file in embedding_files:
                    file_path = os.path.join(speaker_path, file)
                    try:
                        embedding = torch.load(file_path)
                        # Convert to numpy and flatten if needed
                        if isinstance(embedding, torch.Tensor):
                            embedding = embedding.detach().numpy()
                        if embedding.ndim > 1:
                            embedding = embedding.flatten()
                        
                        all_embeddings.append(embedding)
                        speaker_labels.append(f"{accent_dir}_{gender_dir}_{speaker_dir}")
                        accent_labels.append(accent_dir[:3])  # for visualization purposes, do not need the complete folder name
                    except Exception as e:
                        print(f"Error loading {file_path}: {e}")
    
    return np.array(all_embeddings), np.array(speaker_labels), np.array(accent_labels)

def run_kmeans_clustering(embeddings, speaker_labels, num_speakers, output_dir):
    os.makedirs(output_dir, exist_ok=True)
    
    kmeans = KMeans(n_clusters=num_speakers, random_state=42, n_init=10)
    cluster_labels = kmeans.fit_predict(embeddings)
    
    # Evaluate clustering
    homogeneity = homogeneity_score(speaker_labels, cluster_labels)
    completeness = completeness_score(speaker_labels, cluster_labels)
    v_measure = v_measure_score(speaker_labels, cluster_labels)
    
    print(f"Homogeneity: {homogeneity:.4f}")
    print(f"Completeness: {completeness:.4f}")
    print(f"V-measure: {v_measure:.4f}")
    
    cluster_to_speakers = {}
    for i, cluster in enumerate(cluster_labels):
        if cluster not in cluster_to_speakers:
            cluster_to_speakers[cluster] = []
        cluster_to_speakers[cluster].append(speaker_labels[i])
    
    # calculate purity
    total_correct = 0
    for cluster, speakers in cluster_to_speakers.items():
        speaker_counts = {}
        for speaker in speakers:
            if speaker not in speaker_counts:
                speaker_counts[speaker] = 0
            speaker_counts[speaker] += 1
        
        # The dominant speaker is the one with the most occurrences
        dominant_speaker = max(speaker_counts, key=speaker_counts.get)
        total_correct += speaker_counts[dominant_speaker]
    
    purity = total_correct / len(speaker_labels)
    print(f"Cluster purity: {purity:.4f}")
        
    # Save cluster evaluation metrics
    metrics = {
        'homogeneity': homogeneity,
        'completeness': completeness,
        'v_measure': v_measure,
        'purity': purity
    }
    
    pd.DataFrame([metrics]).to_csv(os.path.join(output_dir, 'cluster_metrics.csv'), index=False)
    
    return metrics, cluster_labels

root_directory = "data/ABI-3_Corpus/accents"
output_directory = "results/clustering_analysis"

embeddings, speaker_labels, accent_labels = collect_embeddings_for_clustering(root_directory)

num_speakers = len(np.unique(speaker_labels))
print(f"Total unique speakers: {num_speakers}")

metrics, cluster_labels = run_kmeans_clustering(
    embeddings, 
    speaker_labels, 
    num_speakers, 
    output_directory
)

Total unique speakers: 285
Homogeneity: 0.9763
Completeness: 0.9804
V-measure: 0.9783
Cluster purity: 0.9393


### Cluster visualization

Visualization of only 28 cluster (2 speakers per region, one male and one female).

In [ ]:
def visualize_two_speakers_per_region(embeddings, speaker_labels, accent_labels, output_dir, perplexity=30, n_iter=2000):
    """
    Perform t-SNE on embeddings from two randomly selected speakers per accent region,
    using different shapes for males and females.
    """
    from sklearn.manifold import TSNE
    import matplotlib.pyplot as plt
    import numpy as np
    import random
    import os

    random.seed(42)
    
    os.makedirs(output_dir, exist_ok=True)

    unique_accents = np.unique(accent_labels)
    
    # For each accent, select two speakers
    selected_speakers = []
    for accent in unique_accents:
        male_selected = False
        female_selected = False
        speakers_from_region = []
        # Find all speakers from this accent
        accent_mask = accent_labels == accent
        speakers_in_accent = speaker_labels[accent_mask]
        unique_speakers_in_accent = np.unique(speakers_in_accent)
        
        for speaker in unique_speakers_in_accent: # select one male and one female per accent
            if speaker.split('_')[2] == "male" and not male_selected:
                male_speakers = [s for s in unique_speakers_in_accent if s.split('_')[2] == "male"]
                speakers_from_region.extend(random.sample(male_speakers, 1))
                male_selected = True
            if speaker.split('_')[2] == "female" and not female_selected:
                female_speakers = [s for s in unique_speakers_in_accent if s.split('_')[2] == "female"]
                speakers_from_region.extend(random.sample(female_speakers, 1))
                female_selected = True
            
        selected_speakers.extend(speakers_from_region)
    
    mask = np.isin(speaker_labels, selected_speakers)
    subset_embeddings = embeddings[mask]
    subset_labels = speaker_labels[mask]
    
    print(f"Running t-SNE with perplexity={perplexity}, n_iter={n_iter}")
    tsne = TSNE(n_components=2, perplexity=perplexity, n_iter=n_iter, random_state=42)
    embeddings_tsne = tsne.fit_transform(subset_embeddings)
    
    plt.figure(figsize=(14, 12))
    
    unique_subset_speakers = np.unique(subset_labels)
    cmap = plt.cm.get_cmap('tab20', len(unique_subset_speakers))
    
    for i, speaker in enumerate(unique_subset_speakers):
        parts = speaker.split('_')
        accent = parts[0]
        gender = parts[2]
        speaker_id = parts[3]
        
        # Use different marker shapes based on gender
        marker = 'x' if gender == 'female' else 'o'
        
        speaker_mask = subset_labels == speaker
        plt.scatter(
            embeddings_tsne[speaker_mask, 0],
            embeddings_tsne[speaker_mask, 1],
            label=f"{accent}_{gender[0]}_{speaker_id}",  # Format as accent_g_speakerid for brevity
            color=cmap(i),
            marker=marker,
            alpha=0.7,
            s=50
        )
    
    plt.xlabel("t-SNE Component 1", fontsize=16)
    plt.ylabel("t-SNE Component 2", fontsize=16)
    plt.legend(
        bbox_to_anchor=(1.05, 1.02),
        loc='upper left',
        fontsize=16,       
        labelspacing=0.7,
        borderpad=1.0
    )
    plt.tight_layout()
    plt.savefig(os.path.join(output_dir, 'tsne_two_speakers_per_region.png'), bbox_inches='tight')
    plt.close()
    
    print(f"t-SNE visualization saved to {output_dir}")

visualize_two_speakers_per_region(
    embeddings,
    speaker_labels,
    accent_labels,
    output_directory,
    perplexity=30,
    n_iter=2000
)

Running t-SNE with perplexity=30, n_iter=2000


/home/andrea-gariboldi/anaconda3/envs/speech_env/lib/python3.10/site-packages/sklearn/manifold/_t_sne.py:1164: FutureWarning: 'n_iter' was renamed to 'max_iter' in version 1.5 and will be removed in 1.7.
  warnings.warn(
/tmp/ipykernel_10832/1977297282.py:53: MatplotlibDeprecationWarning: The get_cmap function was deprecated in Matplotlib 3.7 and will be removed in 3.11. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap()`` or ``pyplot.get_cmap()`` instead.
  cmap = plt.cm.get_cmap('tab20', len(unique_subset_speakers))


t-SNE visualization saved to results/clustering_analysis
